<a href="https://colab.research.google.com/github/alby1976/Data607608Project/blob/master/notebook/608/Data608_Group_Prject.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Tracking America's Homicides: Apprehending the Next Serial Killer
## Data 608 Project Code: Winter 2021


Group Members: Graeme Kempthorne, Li Lam, Albert Leung, Yu Nakamura

Ideas for pattern recognition and/or identifying anomalies:
* using classical clustering methods and see with regions are deemed to be an anomality
* using neural networks to do the above.
* using PCA to see which features are "unimportant" and cluster based on those features and see what pattern forms



## Setup

In [ ]:
!pip install nbconvert
!apt-get update
!apt-get install pandoc 
!add-apt-repository universe
!add-apt-repository ppa:inkscape.dev/stable
!apt-get update
!apt install inkscape
!apt-get install texlive-xetex texlive-fonts-recommended texlive-generic-recommended
!jupyter nbconvert DATA_607__Assignment_1.ipynb --to pdf

ERROR: Operation cancelled by user
Get:1 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Hit:2 http://archive.ubuntu.com/ubuntu bionic InRelease
Get:3 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Get:4 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease [3,626 B]
Get:5 http://archive.ubuntu.com/ubuntu bionic-backports InRelease [74.6 kB]
Get:6 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease [15.9 kB]
Hit:7 http://ppa.launchpad.net/cran/libgit2/ubuntu bionic InRelease
Hit:8 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu bionic InRelease
Hit:9 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu bionic InRelease
Ign:10 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Ign:11 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:12 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release
Hit:13 h

In [ ]:
import gc

filedir = '/content/drive/MyDrive/Project 607!608/data/data608/'
if filedir.endswith('/') != True:
  filedir += '/'
  

In [ ]:
!pip install scikit-learn --upgrade

     |████████████████████████████████| 22.3MB 64.8MB/s 
  Found existing installation: scikit-learn 0.22.2.post1
    Uninstalling scikit-learn-0.22.2.post1:
      Successfully uninstalled scikit-learn-0.22.2.post1


In [ ]:
#mount Google drive
from google.colab import drive
from os.path import join
ROOT = '/content/drive' # default for the drive
print(ROOT)
drive.mount(ROOT) # we mount the drive at /content/drive

/content/drive
Mounted at /content/drive


In [ ]:
# for github comit
import os
os.chdir('/content/drive/MyDrive/Project 607!608')

!curl -s https://packagecloud.io/install/repositories/github/git-lfs/script.deb.sh | sudo bash
!sudo apt-get install git-lfs
!git lfs install


Detected operating system as Ubuntu/bionic.
Checking for curl...
Detected curl...
Checking for gpg...
Detected gpg...
Running apt-get update... done.
Installing apt-transport-https... done.
Installing /etc/apt/sources.list.d/github_git-lfs.list...done.
Importing packagecloud gpg key... done.
Running apt-get update... done.

The repository is setup! You can now install packages.
Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following NEW packages will be installed:
  git-lfs
0 upgraded, 1 newly installed, 0 to remove and 46 not upgraded.
Need to get 6,229 kB of archives.
After this operation, 14.5 MB of additional disk space will be used.
Get:1 https://packagecloud.io/github/git-lfs/ubuntu bionic/main amd64 git-lfs amd64 2.13.3 [6,229 kB]
Fetched 6,229 kB in 1s (7,449 kB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is installed, so the dialog based frontend cannot be used. at /usr/share/pe

## Data Wrangling & Modeling

### State Level - Anomaly detection

#### Load State Census Data

In [ ]:
import pandas as pd
import numpy as np

df = pd.read_csv(filedir + 'Cleaned file - MAP, US census/MAP_UScensus_state_merge.csv')
df.dropna(axis=0, how='any', subset=['Population'], inplace=True)


##### Isolation Forest All years - with replacement

In [ ]:
%%time
from sklearn.ensemble import IsolationForest
from sklearn.model_selection import train_test_split

X = df.drop(['State','Year','Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18'], axis=1)
y = df.loc[:,('Year')]
pop = df.loc[:,('Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18')]
X_norm = X.multiply(pop.Population_Fraction, axis=0)  

#X_train, X_test, y_train, y_test = train_test_split(X_norm, y, test_size=0.2, random_state=42, stratify=y)
y_pred = np.empty(y.shape)
y_pred = y_pred[:,np.newaxis]
display(y_pred.shape)

for i in np.arange(0.05, 1.01, 0.05):
  clf = IsolationForest(max_features = i, bootstrap=True, verbose=3, random_state=42)
  result = clf.fit_predict(X_norm)
  y_pred = np.append(y_pred, result[:,np.newaxis], axis=1)

#display(y_pred.mean(axis=1).shape)
X_norm['State'] = df.State
X_norm['Year'] = df.Year
X_norm['Outlier'] = y_pred.mean(axis=1)
X_norm.to_csv(filedir + '/Models/MAP_outliers.csv', index=False)



(997, 1)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Building estimator 1 of 100 for this parallel run (total 100)...
Building estimator 2 of 100 for this parallel run (total 100)...
Building estimator 3 of 100 for this parallel run (total 100)...
Building estimator 4 of 100 for this parallel run (total 100)...
Building estimator 5 of 100 for this parallel run (total 100)...
Building estimator 6 of 100 for this parallel run (total 100)...
Building estimator 7 of 100 for this parallel run (total 100)...
Building estimator 8 of 100 for this parallel run (total 100)...
Building estimator 9 of 100 for this parallel run (total 100)...
Building estimator 10 of 100 for this parallel run (total 100)...
Building estimator 11 of 100 for this parallel run (total 100)...
Building estimator 12 of 100 for this parallel run (total 100)...
Building estimator 13 of 100 for this parallel run (total 100)...
Building estimator 14 of 100 for this parallel run (total 100)...
Building estimator 15 of 100 for this parallel run (total 100)...
Building estimator 

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Building estimator 1 of 100 for this parallel run (total 100)...
Building estimator 2 of 100 for this parallel run (total 100)...
Building estimator 3 of 100 for this parallel run (total 100)...
Building estimator 4 of 100 for this parallel run (total 100)...
Building estimator 5 of 100 for this parallel run (total 100)...
Building estimator 6 of 100 for this parallel run (total 100)...
Building estimator 7 of 100 for this parallel run (total 100)...
Building estimator 8 of 100 for this parallel run (total 100)...
Building estimator 9 of 100 for this parallel run (total 100)...
Building estimator 10 of 100 for this parallel run (total 100)...
Building estimator 11 of 100 for this parallel run (total 100)...
Building estimator 12 of 100 for this parallel run (total 100)...
Building estimator 13 of 100 for this parallel run (total 100)...
Building estimator 14 of 100 for this parallel run (total 100)...
Building estimator 15 of 100 for this parallel run (total 100)...
Building estimator 

...

Building estimator 1 of 100 for this parallel run (total 100)...
Building estimator 2 of 100 for this parallel run (total 100)...
Building estimator 3 of 100 for this parallel run (total 100)...
Building estimator 4 of 100 for this parallel run (total 100)...
Building estimator 5 of 100 for this parallel run (total 100)...
Building estimator 6 of 100 for this parallel run (total 100)...
Building estimator 7 of 100 for this parallel run (total 100)...
Building estimator 8 of 100 for this parallel run (total 100)...
Building estimator 9 of 100 for this parallel run (total 100)...
Building estimator 10 of 100 for this parallel run (total 100)...
Building estimator 11 of 100 for this parallel run (total 100)...
Building estimator 12 of 100 for this parallel run (total 100)...
Building estimator 13 of 100 for this parallel run (total 100)...
Building estimator 14 of 100 for this parallel run (total 100)...
Building estimator 15 of 100 for this parallel run (total 100)...
Building estimator 

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Building estimator 56 of 100 for this parallel run (total 100)...
Building estimator 57 of 100 for this parallel run (total 100)...
Building estimator 58 of 100 for this parallel run (total 100)...
Building estimator 59 of 100 for this parallel run (total 100)...
Building estimator 60 of 100 for this parallel run (total 100)...
Building estimator 61 of 100 for this parallel run (total 100)...
Building estimator 62 of 100 for this parallel run (total 100)...
Building estimator 63 of 100 for this parallel run (total 100)...
Building estimator 64 of 100 for this parallel run (total 100)...
Building estimator 65 of 100 for this parallel run (total 100)...
Building estimator 66 of 100 for this parallel run (total 100)...
Building estimator 67 of 100 for this parallel run (total 100)...
Building estimator 68 of 100 for this parallel run (total 100)...
Building estimator 69 of 100 for this parallel run (total 100)...
Building estimator 70 of 100 for this parallel run (total 100)...
Building e

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s finished


CPU times: user 5.96 s, sys: 368 ms, total: 6.33 s
Wall time: 6.77 s


In [ ]:
%%time
from sklearn.ensemble import IsolationForest
from sklearn.model_selection import train_test_split

X = df.drop(['State','Year','Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18'], axis=1)
y = df.loc[:,('Year')]
pop = df.loc[:,('Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18')]
X_norm = X.multiply(pop.Population_Fraction, axis=0)  

#X_train, X_test, y_train, y_test = train_test_split(X_norm, y, test_size=0.2, random_state=42, stratify=y)
y_pred = np.empty(y.shape)
y_pred = y_pred[:,np.newaxis]
display(y_pred.shape)

for i in np.arange(0.05, 1.01, 0.05):
  clf = IsolationForest(n_jobs = -1, max_features = i, bootstrap=True, verbose=3, random_state=42)
  result = clf.fit_predict(X_norm)
  y_pred = np.append(y_pred, result[:,np.newaxis], axis=1)

#display(y_pred.mean(axis=1).shape)
X_norm['State'] = df.State
X_norm['Year'] = df.Year
X_norm['Outlier'] = y_pred.mean(axis=1)
X_norm.to_csv(filedir + 'Models/MAP_outliers.csv', index=False)



(997, 1)

[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...Building estimator 4 of 50 for this parallel run (total 100)...

Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 9 of 50 for this para

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 9 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 10 of 50 for this parallel run (total 100)...
Building estimator 11 of 50 for this parallel run (total 100)...Building estimator 8 of 50 for this parallel run (total 100)...

Building estimator 9 of 50 for this parallel run (total 100)...
Building estimator 12 of 50 for this parallel run (total 100)...
Building estimator 10 of 50 for this parallel run (total 100)...
Building estimator 11 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 12 of 50 for this parallel run (total 100)...
Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for 

...

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 9 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 9 of 50 for this parallel run (total 100)...
Building estimator 10 of 50 for this parallel run (total 100)...
Building estimator 10 of 50 for this parallel run (total 100)...
Building estimator 11 of 50 for this parallel run (total 100)...
Building estimator 11 of 50 for this parallel run (total 100)...
Building estimator 12 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...Building estimator 12 of 50 for this parallel run (total 100)...

Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for 

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.



Building estimator 12 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...Building estimator 16 of 50 for this parallel run (total 100)...

Building estimator 17 of 50 for this parallel run (total 100)...
Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 18 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 19 of 50 for this parallel run (total 100)...
Building estimator 16 of 50 for this parallel run (total 100)...
Building estimator 17 of 50 for this parallel run (total 100)...Building estimator 20 of 50 for this parallel run (total 100)...
Building estimator 21 of 50 for this parallel run (total 100)...

Building estimator 22 of

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.2s finished


##### Isolation Forest - all years without replacement

In [ ]:
from sklearn.ensemble import IsolationForest
from sklearn.model_selection import train_test_split

X = df.drop(['State','Year','Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18'], axis=1)
y = df.loc[:,('Year')]
pop = df.loc[:,('Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18')]
X_norm = X.multiply(pop.Population_Fraction, axis=0)  

y_pred = np.empty(y.shape)
y_pred = y_pred[:,np.newaxis]

for i in np.arange(0.05, 1.01, 0.05):
  clf = IsolationForest(n_jobs = -1, max_features = i, bootstrap=False, verbose=10, random_state=42)
  result = clf.fit_predict(X_norm)
  y_pred = np.append(y_pred, result[:,np.newaxis], axis=1)

X_norm['State'] = df.State
X_norm['Year'] = df.Year
X_norm['Outlier'] = y_pred.mean(axis=1)
X_norm.to_csv(filedir + 'Models/MAP_outliers_noreplacement.csv', index=False)


[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...Building estimator 8 of 50 for this paral

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 9 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 10 of 50 for this parallel run (total 100)...
Building estimator 9 of 50 for this parallel run (total 100)...
Building estimator 11 of 50 for this parallel run (total 100)...
Building estimator 12 of 50 for this parallel run (total 100)...
Building estimator 10 of 50 for this parallel run (total 100)...
Building estimator 11 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 12 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 for

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


...

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this para

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.



Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 9 of 50 for this parallel run (total 100)...
Building estimator 9 of 50 for this parallel run (total 100)...
Building estimator 10 of 50 for this parallel run (total 100)...Building estimator 10 of 50 for this parallel run (total 100)...

Building estimator 11 of 50 for this parallel run (total 100)...
Building estimator 11 of 50 for this parallel run (total 100)...
Building estimator 12 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 12 of 50 for this parallel run (total 100)...
Building estimator 14 of 50 for this parallel run (total 100)...Building estimator 13 of 50 for this parallel run (total 100)...

Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s remaining:    0.0s
[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished


##### Isolation Forest - By year (with replacemnt)

In [ ]:
from sklearn.ensemble import IsolationForest
from sklearn.model_selection import train_test_split

y = df.loc[:,('Year')]
pop = df.loc[:,('Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18')]
X = df.drop(['State','Year','Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18'], axis=1)
X_norm = X.multiply(pop.Population_Fraction, axis=0)  

outliers = np.empty(y.shape)
for i in range(2000, 2020):
  y_pred = np.empty(y[y==i].shape)
  y_pred = y_pred[:,np.newaxis]
  tmp = X_norm[y==i]
  for j in np.arange(0.05, 1.01, 0.05):
    clf = IsolationForest(n_jobs = -1, max_features = j, bootstrap=True, verbose=2, random_state=42)
    result = clf.fit_predict(tmp)
    y_pred = np.append(y_pred, result[:,np.newaxis], axis=1)
  outliers[y == i] = y_pred.mean(axis=1)

X_norm['State'] = df.State
X_norm['Year'] = df.Year
X_norm['Outlier'] = outliers
X_norm.to_csv(filedir + 'Models/MAP_outliers_by_year.csv', index=False)


[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...Building estimator 3 of 50 for this parallel run (total 100)...

Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...Building estimator 7 of 50 for this parallel run (total 100)...

Building estimator 9 of 50 for this para

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 10 of 50 for this parallel run (total 100)...
Building estimator 11 of 50 for this parallel run (total 100)...
Building estimator 11 of 50 for this parallel run (total 100)...
Building estimator 12 of 50 for this parallel run (total 100)...Building estimator 12 of 50 for this parallel run (total 100)...

Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 14 of 50 for this parallel run (total 100)...Building estimator 14 of 50 for this parallel run (total 100)...

Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 16 of 50 for this parallel run (total 100)...
Building estimator 17 of 50 for this parallel run (total 100)...Building estimator 16 of 50 for this parallel run (total 100)...

Building estimator 18 of 50 for this parallel run (total 100)...
Building estimator 17 of 

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.2s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


...

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 13 of 50 for this parallel run (total 100)...

Building estimator 12 of 50 for this parallel run (total 100)...Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 16 of 50 for this parallel run (total 100)...

Building estimator 15 of 50 for this parallel run (total 100)...Building estimator 17 of 50 for this parallel run (total 100)...

Building estimator 18 of 50 for this parallel run (total 100)...Building estimator 16 of 50 for this parallel run (total 100)...

Building estimator 17 of 50 for this parallel run (total 100)...Building estimator 19 of 50 for this parallel run (total 100)...
Building estimator 18 of 50 for this parallel run (total 100)...
Building estimator 20 of 50 for this parallel run (total 100)...
Building estimator 19 of 

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this para

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.2s finished


##### Isolation Forest - By year (without replacement)

In [ ]:
from sklearn.ensemble import IsolationForest
from sklearn.model_selection import train_test_split

y = df.loc[:,('Year')]
pop = df.loc[:,('Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18')]
X = df.drop(['State','Year','Population','Population_Fraction','us_pop_Male', 'us_pop_Female', 'us_pop_+18', 'us_pop_<18'], axis=1)
X_norm = X.multiply(pop.Population_Fraction, axis=0)  

outliers = np.empty(y.shape)
for i in range(2000, 2020):
  y_pred = np.empty(y[y==i].shape)
  y_pred = y_pred[:,np.newaxis]
  tmp = X_norm[y==i]
  for j in np.arange(0.05, 1.01, 0.05):
    clf = IsolationForest(n_jobs = -1, max_features = j, bootstrap=True, verbose=2, random_state=42)
    result = clf.fit_predict(tmp)
    y_pred = np.append(y_pred, result[:,np.newaxis], axis=1)
  outliers[y == i] = y_pred.mean(axis=1)

X_norm['State'] = df.State
X_norm['Year'] = df.Year
X_norm['Outlier'] = outliers
X_norm.to_csv(filedir + '/Models/MAP_outliers_year_noreplacement.csv', index=False)



[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...

Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...

Building estimator 6 of 50 for this parallel run (total 100)...Building estimator 7 of 50 for this parallel run (total 100)...

Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 8 of 50 for this parallel run (total 100)...
Building estimator 9 of 50 for this para

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 16 of 50 for this parallel run (total 100)...
Building estimator 17 of 50 for this parallel run (total 100)...
Building estimator 12 of 50 for this parallel run (total 100)...
Building estimator 18 of 50 for this parallel run (total 100)...
Building estimator 19 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 20 of 50 for this parallel run (total 100)...
Building estimator 21 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 22 of 50 for this parallel run (total 100)...
Building estimator 23 of 50 for this parallel run (total 100)...
Building estimator 24 of 50 for this parallel run (total 100)...
Building estimator 16 of 50 for this parallel run (total 100)...
Building estimator 25 of 

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


...

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 13 of 50 for this parallel run (total 100)...
Building estimator 16 of 50 for this parallel run (total 100)...Building estimator 14 of 50 for this parallel run (total 100)...
Building estimator 17 of 50 for this parallel run (total 100)...
Building estimator 15 of 50 for this parallel run (total 100)...
Building estimator 18 of 50 for this parallel run (total 100)...
Building estimator 16 of 50 for this parallel run (total 100)...
Building estimator 19 of 50 for this parallel run (total 100)...
Building estimator 17 of 50 for this parallel run (total 100)...
Building estimator 20 of 50 for this parallel run (total 100)...
Building estimator 18 of 50 for this parallel run (total 100)...
Building estimator 21 of 50 for this parallel run (total 100)...
Building estimator 19 of 50 for this parallel run (total 100)...
Building estimator 22 of 5

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 1 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 2 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 3 of 50 for this parallel run (total 100)...
Building estimator 4 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 5 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 6 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...
Building estimator 7 of 50 for this parallel run (total 100)...Building estimator 8 of 50 for this parallel run (total 100)...

Building estimator 9 of 50 for this para

[Parallel(n_jobs=2)]: Done   2 out of   2 | elapsed:    0.2s finished


### County Level

#### Common variables and functions

In [ ]:
import pandas as pd
import numpy as np

def convert (df, colname, lookup):
  df.loc[df[colname] == lookup[0], colname] = lookup[1]
  return df

def convert_list (df, colname, lookups):
  for lookup in lookups:
    df = convert(df, colname, lookup)
  return df

# Conversion array
agegroup = zip([x for x in range (0, 19)], ['Total', 
  'Age 0 to 4 years', 
  'Age 5 to 9 years', 
  'Age 10 to 14 years',
  'Age 15 to 19 years', 
  'Age 20 to 24 years', 
  'Age 25 to 29 years', 
  'Age 30 to 34 years', 
  'Age 35 to 39 years', 
  'Age 40 to 44 years', 
  'Age 45 to 49 years', 
  'Age 50 to 54 years', 
  'Age 55 to 59 years', 
  'Age 60 to 64 years', 
  'Age 65 to 69 years', 
  'Age 70 to 74 years', 
  'Age 75 to 79 years', 
  'Age 80 to 84 years', 
  'Age 85 years or older'])

def calculate_agegroup(age):
  if age == 999:
    return 0
  elif age >= 85:
    return 18
  else:
    return (age // 5) + 1

def calculate_anomaly (features, size, start=0.05, stop=1.01, step=0.05, bootstrap=True, verbose=0, random_state=42):
  y_pred = np.empty(size)
  y_pred = y_pred[:,np.newaxis]
  for j in np.arange(start, stop, step):
    if j >= 1:
      j = 1
    print('\n', f'j: {j}')
    clf = IsolationForest(n_jobs = -1, max_features = j, bootstrap=bootstrap, verbose=verbose, random_state=random_state)
    result = clf.fit_predict(features)
    y_pred = np.append(y_pred, result[:,np.newaxis], axis=1)
  return y_pred.mean(axis=1)



#### Load Murder Data

In [ ]:
import pandas as pd
# conversion array
solved = zip(['Yes', 'No'],[True, False])
month = zip(['January', 'February', 'March', 'April', 'May','June', 'July', 'August', 'September','October', 'November', 'December'], [x for x in range(1,13)])

murder = pd.read_csv(filedir + 'SHR76_19.csv')
murder.to_parquet('SHR76_19.parquet', index=False)
murder = pd.read_parquet('SHR76_19.parquet')
loc = murder[['State','CNTYFIPS']]
murder.drop(columns=['ID','CNTYFIPS','Ori','State'], inplace=True)
murder = murder.loc[murder.Year >= 2000, :]
ages = murder.VicAge
murder['VicAgeGroup'] = [calculate_agegroup(age) for age in ages] 
ages = murder.OffAge
murder['OffAgeGroup'] = [calculate_agegroup(age) for age in ages]
murder.VicCount += 1
murder.OffCount += 1
murder = convert_list(murder,'Solved', solved)
murder = convert_list(murder,'Month', month)
murder.Month = murder.Month.apply(pd.to_numeric)
#murder.FileDate = pd.to_datetime(murder.FileDate, format='%m%d%y')


##### Transforming Individual Cases

In [ ]:
from sklearn import preprocessing

def convert_col_name (col_name, names):
  tmp = col_name.split('_', maxsplit=1)
  idx = int(tmp[0].split('x')[1])
  return '__'.join([names[idx],tmp[1].replace(' ','_')])

#drop the second dummy variable column if dummy variable is binary
enc = preprocessing.OneHotEncoder(sparse=True, drop='if_binary')


#get categorical variables
cat = murder.select_dtypes(include=[object])
names = cat.columns
#get numerical variables
num = murder.select_dtypes(exclude=[object])
#transforms the categorial variables into dummy variables
cat = enc.fit_transform(cat)
#the result of the transformation is a sparse maxtrix so convert it into pd.DataFrame
cat = pd.DataFrame.sparse.from_spmatrix(cat,columns=enc.get_feature_names())
#converts the column names back to their corresponding categorial variable names
cat.columns = [convert_col_name(col_name, names) for col_name in enc.get_feature_names()]
#set the index of the new Dataframe to be the same as the original DataFrame for concatenation purposes
cat.index = murder.index
#concat allow the column axis
murder = pd.concat([num,cat], axis=1)
del names, cat
display (murder)

FIPS  ...  Subcircum__None
446      2020  ...              1.0
447      2020  ...              1.0
448      2020  ...              1.0
449      2020  ...              1.0
450      2020  ...              1.0
...       ...  ...              ...
804746  56013  ...              1.0
804747  56013  ...              1.0
804748  56013  ...              1.0
804749  56013  ...              1.0
804750  56013  ...              1.0

[324504 rows x 8046 columns]

###### Isolation Forest By years - with replacemnt

In [ ]:
from sklearn.ensemble import IsolationForest
from scipy.sparse import csr_matrix

X = murder.drop(['Year'], axis=1)
X.fillna(-1, inplace=True)
y = murder.Year
outliers = np.empty(y.shape)
for i in range(2000, 2020):
  print('\n',f'Year: {i} tmp: {X[y==i].shape} outliers: {(outliers[y==i]).shape}','\n')
  outliers[y==i] = calculate_anomaly(csr_matrix(X[y==i].values), outliers[y==i].shape, start=0.1, step=0.1, verbose=1)
  gc.collect()

del X
num['State'] = loc.State
num['County'] = loc.CNTYFIPS
num['Outlier'] = outliers
print('writing to file')
num.to_csv(filedir + 'Models/MAP_county_outliers_by_year.csv', index=False)



 Year: 2000 tmp: (14692, 8045) outliers: (14692,) 


 j: 0.1


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.5s remaining:    0.5s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.5s finished



 j: 0.2


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.5s remaining:    0.5s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.5s finished



 j: 0.30000000000000004


...


 j: 0.9


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.7s remaining:    0.7s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.7s finished



 j: 1


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.4s remaining:    0.4s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.4s finished


writing to file


###### Isolation Forest By years - without replacemnt

In [ ]:
;;;;;;;;;;;;;;;;from sklearn.ensemble import IsolationForest
from scipy.sparse import csr_matrix

X = murder.drop(['Year'], axis=1)
X.fillna(-1, inplace=True)
y = murder.Year
outliers = np.empty(y.shape)
for i in range(2000, 2020):
  print('\n',f'Year: {i} tmp: {X[y==i].shape} outliers: {(outliers[y==i]).shape}','\n')
  outliers[y==i] = calculate_anomaly(csr_matrix(X[y==i].values), outliers[y==i].shape, start=0.1, step=0.1, bootstrap=False, verbose=1)
  gc.collect()

del X
num['State'] = loc.State
num['County'] = loc.CNTYFIPS
num['Outlier'] = outliers
print('writing to file')
num.to_csv(filedir + 'Models/MAP_county_outliers_by_year_without_replacement.csv', index=False)



 Year: 2000 tmp: (14692, 8045) outliers: (14692,) 


 j: 0.1


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.5s remaining:    0.5s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.6s finished



 j: 0.2


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.6s remaining:    0.6s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.6s finished



 j: 0.30000000000000004


...


 j: 0.9


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.7s remaining:    0.7s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.7s finished



 j: 1


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.4s remaining:    0.4s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.4s finished



 Year: 2010 tmp: (15133, 8045) outliers: (15133,) 


 j: 0.1


###### Isolation Forest - with replacement

In [ ]:
from sklearn.ensemble import IsolationForest
from scipy.sparse import csr_matrix

X = murder.drop(['Year'], axis=1)
X.fillna(-1, inplace=True)
y = murder.Year

outliers = np.empty(y.shape)
print('\n',f'Year: {i} tmp: {X.shape} outliers: {y.shape}','\n')
outliers = calculate_anomaly(csr_matrix(X.values), y.shape, start=0.1, step=0.1, verbose=1)
gc.collect()

del X
num['State'] = loc.State
num['County'] = loc.CNTYFIPS
num['Year'] = murder.Year
num['Outlier'] = outliers
print('writing to file')
num.to_csv(filedir + 'Models/MAP_county_outliers.csv', index=False)



 Year: 2019 tmp: (324504, 8045) outliers: (324504,) 


 j: 0.1


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    1.4s remaining:    1.4s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    1.5s finished



 j: 0.2


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    2.0s remaining:    2.0s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    2.1s finished



 j: 0.30000000000000004


...


 j: 0.9


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    5.4s remaining:    5.4s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    5.5s finished



 j: 1


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.6s remaining:    0.6s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.6s finished


writing to file


###### Isolation Forest - without replacement

In [ ]:
from sklearn.ensemble import IsolationForest
from scipy.sparse import csr_matrix

X = murder.drop(['Year'], axis=1)
X.fillna(-1, inplace=True)
y = murder.Year
outliers = np.empty(y.shape)
print('\n',f'Year: {i} tmp: {X.shape} outliers: {y.shape}','\n')
outliers = calculate_anomaly(csr_matrix(X.values), y.shape, start=0.1, step=0.1, bootstrap=False, verbose=1)
gc.collect()

del X
num['State'] = loc.State
num['County'] = loc.CNTYFIPS
num['Year'] = murder.Year
num['Outlier'] = outliers
print('writing to file')
num.to_csv(filedir + 'Models/MAP_county_outliers_without_replacement.csv', index=False)



 Year: 2019 tmp: (324504, 8045) outliers: (324504,) 


 j: 0.1


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    1.3s remaining:    1.3s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    1.3s finished



 j: 0.2


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    1.6s remaining:    1.6s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    1.7s finished



 j: 0.30000000000000004


...


 j: 0.9


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    3.8s remaining:    3.8s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    4.0s finished



 j: 1


[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   2 out of   4 | elapsed:    0.7s remaining:    0.7s
[Parallel(n_jobs=4)]: Done   4 out of   4 | elapsed:    0.7s finished


writing to file


#### Web Scraping - County level Census Data (2000 - 2019)

In [ ]:
from bs4 import BeautifulSoup
import pandas as pd
import requests

urls = ['https://www2.census.gov/programs-surveys/popest/datasets/2000-2009/counties/asrh/','https://www2.census.gov/programs-surveys/popest/datasets/2010-2019/counties/asrh/']
for url in urls:
  source = requests.get(url)
  soup = BeautifulSoup(source.content)
  for link in soup.find_all('a'):
    if '.csv' in link.text:
      href = link['href']
      print(url+format(href))
      if os.path.exists(href) != True:
        try:
          data = pd.read_csv(url+format(href))
        except:
          data = pd.read_csv(url+format(href), encoding='cp1252')
        data.to_csv('./' + href)
    

##### Combine Census Data

In [ ]:
import pandas as pd
import numpy as np
import glob

#conversion array
year2009 = zip([x for x in range (3, 13)], [x for x in range (2000, 2010)])
year2019 = zip([x for x in range (3, 13)], [x for x in range (2010, 2020)])

tmp = pd.concat([pd.read_csv(f) for f in glob.glob('/content/drive/MyDrive/Project 607!608/census/combined/*2009*.csv')], ignore_index = True)
tmp.drop(columns=['Unnamed: 0','SUMLEV'], inplace=True)
tmp = tmp.loc[tmp.YEAR > 2, :]
for year in year2009: 
  tmp = convert(tmp, 'YEAR', year)

tmp1 = pd.concat([pd.read_csv(f) for f in glob.glob('/content/drive/MyDrive/Project 607!608/census/combined/*2019*.csv')], ignore_index = True)
tmp1.drop(columns=['Unnamed: 0','SUMLEV'], inplace=True)
tmp1 = tmp1.loc[tmp1.YEAR > 2, :]
for year in year2019: 
  tmp1 = convert(tmp1, 'YEAR', year)

county = pd.concat([tmp, tmp1], ignore_index = True) 
county["FIPS"] = 1000 * county.STATE + county.COUNTY
#display(county.loc[county.AGEGRP == 0,:])
county.drop(columns=['STATE', 'COUNTY', 'STNAME', 'CTYNAME'], inplace=True)
display(county)

#clean up memeory remove tempory variables
del tmp, tmp1


### Merging Murder and Census data

In [ ]:
#murder = murder.groupby(by=['FIPS','Year'], axis=1)
murder = pd.merge(murder, county, how = 'left', left_on=['FIPS', 'Year'], right_on=['FIPS', 'YEAR'])
display(murder)


FIPS             Agency  ... HNAC_MALE HNAC_FEMALE
0         2020          Anchorage  ...       117         143
1         2020          Anchorage  ...        22          31
2         2020          Anchorage  ...        17          24
3         2020          Anchorage  ...        13          26
4         2020          Anchorage  ...        10          15
...        ...                ...  ...       ...         ...
6165337  56013  Wind River Agency  ...         0           0
6165338  56013  Wind River Agency  ...         0           0
6165339  56013  Wind River Agency  ...         1           1
6165340  56013  Wind River Agency  ...         0           0
6165341  56013  Wind River Agency  ...         1           0

[6165342 rows x 103 columns]

In [ ]:
county = convert_list(county, 'AGEGRP', agegroup)
murder = convert_list(murder, 'VicAgeGroup', agegroup)
murder = convert_list(murder, 'OffAgeGroup', agegroup)
county.to_csv('/content/drive/MyDrive/Project 607!608/County/County_census_2000_to_2019.csv', index=False)
murder.to_csv('/content/drive/MyDrive/Project 607!608/County/MAP_wrangled_2000_to_2019.csv', index=False)

In [ ]:
murder.to_csv('/content/drive/MyDrive/Project 607!608/MAP_county_combined.csv',index_label=False)

In [ ]:
print(list(agegroup))

[(0, 'Total'), (1, 'Age 0 to 4 years'), (2, 'Age 5 to 9 years'), (3, 'Age 10 to 14 years'), (4, 'Age 15 to 19 years'), (5, 'Age 20 to 24 years'), (6, 'Age 25 to 29 years'), (7, 'Age 30 to 34 years'), (8, 'Age 35 to 39 years'), (9, 'Age 40 to 44 years'), (10, 'Age 45 to 49 years'), (11, 'Age 50 to 54 years'), (12, 'Age 55 to 59 years'), (13, 'Age 60 to 64 years'), (14, 'Age 65 to 69 years'), (15, 'Age 70 to 74 years'), (16, 'Age 75 to 79 years'), (17, 'Age 80 to 84 years'), (18, 'Age 85 years or older')]
